In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import collections
import random

from salt_bert.make_preprocessed_data import tokenization
from tqdm.notebook import trange, tqdm
import tensorflow.compat.v1 as tf

2021-11-30 13:39:30.262238: I tensorflow/stream_executor/platform/default/dso_loader.cc:49] Successfully opened dynamic library libcudart.so.11.0


In [2]:
tf.logging.set_verbosity(tf.logging.INFO)
# Tokenizer의 initializing (tokenization.py 의 FullTokenizer) --> 해당 tokenizer의 output은 BPE tokenized tokens
# 각 전처리된 vocab_dict를, 숫자화 시켜줌
tokenizer = tokenization.FullTokenizer(vocab_file='./sample_normalize_light_no_enter_preproc.txt', do_lower_case=False)

# 필수 필요파일
input_file = './wiki_preprocess_sample_normalize_enter_small.txt'

# pre-trained에 사용될 데이터를 구함.
input_files = []
for input_pattern in input_file.split(","):
    input_files.extend(tf.gfile.Glob(input_pattern))

# 여기까지 정리해보면, 단어세트(사전)와 문장세트(문서)를 구한 것임.    
# 이후에는 사전을 이용하여, 문서를 해석해나가는 작업을 진행함.
tf.logging.info("*** Reading from input files ***")
for input_file in input_files:
    tf.logging.info("  %s", input_file)

random_seed = 777
rng = random.Random(random_seed)
max_seq_length = 512  # 512가 좋으나, 매우 느려서 128로넣고 512로 넣는걸 추천. 하지만 추가학습으로 그렇게 진행할 시, 나중에 쓸때도 그렇게 써줘야함.
dupe_factor = 1 # 중복된 값의 인풋데이터 (서로 다른 마스크)
short_seq_prob = 0.1 # 맥시멈 렝스보다 짧은 문장을 만들 가능성
masked_lm_prob = 0.15 # 마스킹 비율
max_predictions_per_seq = 20 # [MASK] token의 최대 개수

print('before instance')
# instances = create_training_instances(		# [CLS] 문장 A [SEP] 문장 B [SEP] 꼴을 만들어 줌
#     input_files, tokenizer, max_seq_length, dupe_factor,
#     short_seq_prob, masked_lm_prob, max_predictions_per_seq,
#     rng)
"""Create `TrainingInstance`s from raw text."""
all_documents = [[]]

# Input file format:
# (1) 라인당 1문장. 실제 문장일 것을 권장, 임의의 쪼개진 문장이면 안됨. (다음 문장을 예측하기 위해 사용할 것이므로).
# (2) 문서간에는 공백이 필요함. 공백을 보고 다음문장을 요약하지 않는데 사용할 것임.
cnt = 0
bad_cnt=0
all_cnt=0
tf.logging.info('begin read input file')
for input_file in input_files:
    with open(input_file, 'r', encoding='utf-8') as reader:
#         while True:
        while True:
            cnt += 1    # cnt는 단순히 얼마만큼 됬는지 확인하기 위함
            if(cnt % 50000 == 0):
                tf.logging.info('%d line pass', cnt)
            # 문서에서 깨진 문자열등을 정규화 하기위한 유니코드 변환 작업.
            line = tokenization.convert_to_unicode(reader.readline())
            if not line:
                break
            # 엉뚱한 공백 제거 (문서, 문장 간 공백처리가 매우 중요하다...)
            line = line.strip()

            # 빈 엔터는 문서를 구분짓는데 사용한다.
            if not line:
                all_documents.append([])        # 이중 엔터를 통해 문서를 구분
            # 문서의 각 라인을 유니코드로 변환하고, 잘못된 문자열을 제거하고, 띄어쓰기로 분리하여 한문장의 배열로 만듬. (basic)
            # basic이 끝나면, wrodpiece에서 각 토큰을 전체탐색하면서, bpe를 진행하고, 해당 bpe가 vocab에 있는지 확인 못찾으면 unk처리
            # 딕셔너리로 만든 데이터를 넣는다면, 잘 되었다면, unk이 없거나, 매우 적어야할 것임.
            tokens = tokenizer.tokenize(line)
            if any('[UNK]' in word for word in tokens):
                bad_cnt += 1
            if tokens:
                all_documents[-1].append(tokens)
                # 완성된 문서의 wordpiece 리스트를 만듬
                # all_documents = [["이순신은 ...", "##그는 ..."], ["문재인","##대통령은...", "대한민국.."]]
            all_cnt += 1
        print("bad_cnt per all_cnt : " + str(bad_cnt) + " / " + str(all_cnt))
        # 위키데이터 윗줄부터 180메가로 410메가 돌렸는데 bad_cnt per all_cnt : 360974 / 3133129 이정도 나옴!!!!!!!!!!

# Remove empty documents
tf.logging.info('finish read input file')
all_documents = [x for x in all_documents if x]    # if x: x가 값이 있을 경우에만 all_documents에 list화 --> 빈 document 제거
tf.logging.info('shuffle all documents')
# rng.shuffle(all_documents)			# 문서 단위로 shuffle. 문서의 순서가 중요한경우 셔플하면 안될듯...

INFO:tensorflow:*** Reading from input files ***
INFO:tensorflow:  ./wiki_preprocess_sample_normalize_enter_small.txt
before instance
INFO:tensorflow:begin read input file
INFO:tensorflow:50000 line pass
INFO:tensorflow:100000 line pass
INFO:tensorflow:150000 line pass
bad_cnt per all_cnt : 3348 / 150721
INFO:tensorflow:finish read input file
INFO:tensorflow:shuffle all documents


In [3]:
class TrainingInstance(object):
    """A single training instance (sentence pair)."""

    def __init__(self, tokens, segment_ids, masked_lm_positions, masked_lm_labels,
                 is_random_next):
        self.tokens = tokens
        self.segment_ids = segment_ids
        self.is_random_next = is_random_next
        self.masked_lm_positions = masked_lm_positions
        self.masked_lm_labels = masked_lm_labels

    def __str__(self):
        s = ""
        s += "tokens: %s\n" % (" ".join(
            [tokenization.printable_text(x) for x in self.tokens]))
        s += "segment_ids: %s\n" % (" ".join([str(x)
                                              for x in self.segment_ids]))
        s += "is_random_next: %s\n" % self.is_random_next
        s += "masked_lm_positions: %s\n" % (" ".join(
            [str(x) for x in self.masked_lm_positions]))
        s += "masked_lm_labels: %s\n" % (" ".join(
            [tokenization.printable_text(x) for x in self.masked_lm_labels]))
        s += "\n"
        return s
    
    def __dict__(self):
        s = dict()
        s['tokens']=self.tokens
        s['segment_ids']=self.segment_ids
        s['is_random_next']=self.is_random_next
        s['masked_lm_positions']=self.masked_lm_positions
        s['masked_lm_labels']=self.masked_lm_labels
        return s
    
    def __repr__(self):
        return self.__str__()

In [4]:
def write_instance_to_example_files(instances, tokenizer, max_seq_length,
                                                                        max_predictions_per_seq, output_files):
    """Create TF example files from `TrainingInstance`s."""
    writers = []
    for output_file in output_files:
        writers.append(tf.python_io.TFRecordWriter(output_file))

    writer_index = 0

    total_written = 0
    for (inst_index, instance) in enumerate(tqdm(instances, desc='tf.record.save_setting')):
        input_ids = tokenizer.convert_tokens_to_ids(instance.tokens)
        input_mask = [1] * len(input_ids)
        segment_ids = list(instance.segment_ids)
        assert len(input_ids) <= max_seq_length

        while len(input_ids) < max_seq_length:
            input_ids.append(0)
            input_mask.append(0)
            segment_ids.append(0)

        assert len(input_ids) == max_seq_length
        assert len(input_mask) == max_seq_length
        assert len(segment_ids) == max_seq_length

        masked_lm_positions = list(instance.masked_lm_positions)
        masked_lm_ids = tokenizer.convert_tokens_to_ids(instance.masked_lm_labels)
        masked_lm_weights = [1.0] * len(masked_lm_ids)

        while len(masked_lm_positions) < max_predictions_per_seq:
            masked_lm_positions.append(0)
            masked_lm_ids.append(0)
            masked_lm_weights.append(0.0)

        next_sentence_label = 1 if instance.is_random_next else 0

        features = collections.OrderedDict()
        features["input_ids"] = create_int_feature(input_ids)
        features["input_mask"] = create_int_feature(input_mask)
        features["segment_ids"] = create_int_feature(segment_ids)
        features["masked_lm_positions"] = create_int_feature(masked_lm_positions)
        features["masked_lm_ids"] = create_int_feature(masked_lm_ids)
        features["masked_lm_weights"] = create_float_feature(masked_lm_weights)
        features["next_sentence_labels"] = create_int_feature([next_sentence_label])

        tf_example = tf.train.Example(features=tf.train.Features(feature=features))

        writers[writer_index].write(tf_example.SerializeToString())
        writer_index = (writer_index + 1) % len(writers)

        total_written += 1

        if inst_index < 20:
            tf.logging.info("*** Example ***")
            tf.logging.info("tokens: %s" % " ".join(
                    [tokenization.printable_text(x) for x in instance.tokens]))

            for feature_name in features.keys():
                feature = features[feature_name]
                values = []
                if feature.int64_list.value:
                    values = feature.int64_list.value
                elif feature.float_list.value:
                    values = feature.float_list.value
                tf.logging.info(
                        "%s: %s" % (feature_name, " ".join([str(x) for x in values])))

    for writer in writers:
        writer.close()
        
    tf.logging.info("Wrote %d total instances", total_written)

def create_int_feature(values):
    feature = tf.train.Feature(int64_list=tf.train.Int64List(value=list(values)))
    return feature


def create_float_feature(values):
    feature = tf.train.Feature(float_list=tf.train.FloatList(value=list(values)))
    return feature

In [15]:
def create_instances_from_document(all_documents, document_index, max_seq_length, short_seq_prob,
                                   masked_lm_prob, max_predictions_per_seq, vocab_words, rng):
    """한 문서에 대해 Pre-Training을 위한 BERT Input FIT으로 맞춰준다."""
    document = all_documents[document_index]
    # Account for [CLS], [SEP], [SEP]
    # 512 - 3 input token 개수인 512개에서 필수로 포함되는 3가지 token([CLS], [SEP], [SEP])을 제거
    max_num_tokens = max_seq_length - 3
    # 우리는 패딩을 채워서라도 max_seq_length에 해당하는, 전체 시퀀스를 맞추려고 노력한다.
    # max_seq_length의 관점에서 접근하면, 짧은 문장들은 버려지게 되는데,
    # 어찌됐든, 종종 short_seq_prob 같은걸 써서라도,
    # Pre Training과 Fine-Tuning 사이에 짧은 문장에 대한 오차범위를 줄이고 싶을 수 있다.
    # target_seq_length는 max_seq_length를 써서 강하게 제한을 거는 것 보다는, 비교적으로 널럴하게 제한을 잡을 수 있다.
    target_seq_length = max_num_tokens
    if rng.random() < short_seq_prob:   # 랜덤 추출하더라도, short_seq_prob 보다도 작아서, 짧은 문장 추출이 잘 이루어지지 않을 것 같으면,
        target_seq_length = rng.randint(
            2, max_num_tokens)				# 1. 2-509 만큼 random 선택
        # 509개의 sequence length중, 학습을 위해 채울 sequence length를 dynamic하게 결정 -> 사실상 랜덤이니...
    # A,B 문장구조로 쪼개서 사용해야하는 이유에 대한 설명...
    # 우리는 단순히 문서의 긴 문장에 대한 토큰을 전부 합치는 것은 아니고, 임의적으로 나누는 구간을 정한다.
    # 다음 문장에 대한 예측이 너무 쉬워질 수 있기 때문이다.(overfitting 야기 가능을 이야기 하는듯.)
    # 대신에, 유저의 입력으로 제공되는 실제 문장을 A,B 단위로 쪼개서 사용한다.

    instances = []
    current_chunk = []
    current_length = 0
    i = 0
    while i < len(document):							# 2. 해당 document의 문장들을 가져옴
        segment = document[i]    # 한 문장만 가져옴
        current_chunk.append(segment)						# 3. chunk에 문장을 append
        current_length += len(segment)						# 4. chunk된 문장 길이를 계산
        '''
            token_a와 token_b를 문서에서 선정하게된다.
            유의사항 : token a,b를 만드는 것은, 512 length를 넘겨도 좋으니 일단 채우고 본다.(뒤에서 자른다 294 line)
            token_a와 token_b는 여러문장으로 구성될 수 있다. 또한, token_b의 경우, 문서에서 랜덤으로 선택하다보니, 운좋게 동일하게 나올 수도 있다.
            다만, token_a는 문서의 순서대로 돌아가며 진행되고, 문서를 재사용하지 않으니, 무조건 1회만 등장한다. (dupe_factor 말고, 실제로 만들때.)
        '''
        # 5. 목표치 sequence length에 도달했다면
        if i == len(document) - 1 or current_length >= target_seq_length:
            if current_chunk:
                # `a_end` A에 들어가는 current_chunk가 얼마만큼의 부분으로 이루어져 있을지 구분 짓는 값
                # (first) sentence.
                a_end = 1
                print(current_chunk)
                if len(current_chunk) >= 2:
                    # 6. 문장 A의 끝을 random하게 선택
                    a_end = rng.randint(1, len(current_chunk) - 1)
                    print('a_end : ', a_end)
                tokens_a = []
                for j in range(a_end):
                    tokens_a.extend(current_chunk[j])

                tokens_b = []
                # Random next
                is_random_next = False							# 7. 문장 B를 생성할 예정인데,
                # A가 한문장 들어갔거나, B는 랜덤 생성시킴.
                # 8. token_b로 사용할 수 있는 문장이 1개라도 있던가, 50%의 확률로 걸리면, IsNext or NotNext
                # 정확히는, len(current_chunk)==1을 비교하는 이유는, token_a가 최소 1개는 있어야, token_b를 만드는 것이 의미가 있기 때문이다._ysh_211130
                # 해당 조건문은 len(current_chunk)>=1이어도 무관하다._ysh_211130
                if len(current_chunk) == 1 or rng.random() < 0.5:
                    is_random_next = True
                    # 전체 길이에서 tokens_a문장들만큼의 길이를 뺀다음에, (토큰을 넣을 수 있는 남은 자리를 판단한다.)
                    target_b_length = target_seq_length - \
                        len(tokens_a)

                    # 드물게 긴 말뭉치에서 반복이 한번 더도는 문제가 생기긴 하지만, 데이터 잘 이해하고 돌리면,
                    # 랜덤한 문서를 생성할 수 있다.
                    # 10번을 찍어서 강제로 랜덤한 문서 하나를 선택한다._ysh_211130
                    for _ in range(10):
                        # 랜덤한 문서 하나를 선택함.
                        random_document_index = rng.randint(
                            0, len(all_documents) - 1)
                        # 같은 문서가 아니기만 하면 되니 10번정도 반복시켜봄. 설마 10번안에 계속 걸릴까...
                        if random_document_index != document_index:
                            break

                    # 10. Random으로 다음 문장 선택한 후 붙여줌
                    # random_document에는, 랜덤하게 선택된 문서의 문장배열이 들어간다.(1차원)_ysh_211130
                    # 소스에서 나오는 배열들의 주소를 참조하는 방식이, 1차원으로 접근한다고해서, 무조건 1차원으로 생각하면 안된다._ysh_211130
                    # 왜냐하면, 2차원에서 [0][x]의 형태로 1개를 선택하고나면, 그 이후부터는 더이상 2차원이 아닌 1차원이기 때문이다._ysh_211130
                    random_document = all_documents[random_document_index]
                    # token_b는 문서에서의 시작을 무조건 처음부터 끊는 것이 아닌, 랜덤한 문서에서의 처음 혹은 중간에서부터 뽑고싶어한다.(랜덤으로)_ysh_211130
                    random_start = rng.randint(0, len(random_document) - 1)
                    # token_b를 위한 랜덤하게 선택된 위치에서부터, 문서의 끝까지 for문을 돌면서,_ysh_211130
                    # 문장에서의 단어가 짤리는 경우는 없다. 짤리면 문장이 통째로 짤린다._ysh_211130
                    for j in range(random_start, len(random_document)):
                        tokens_b.extend(random_document[j])
                        # 붙힐 수 있는 최대 length까지 다붙힘. 일단 최대 length보다 길어도 붙히고 본다. 길어진 부분은 밑에서 짜르는 부분이 있다.(294 line)_ysh_211130
                        if len(tokens_b) >= target_b_length:
                            break
                    # A부분 잘라낸 뒷부분은 현재는 랜덤으로 치환될 것이므로, 안쓰게 될텐데, 일단 저장해놓는다.
                    # token_a에서의 a_end를 사용하므로, token_a에서의 남은 뒷영역(token_a는 무조건 시작부터 랜덤위치까지 자르므로,)을 저장하게된다._ysh_211130
                    num_unused_segments = len(current_chunk) - a_end
                    i -= num_unused_segments
                # Actual next
                else:
                    is_random_next = False						# 11. IsNext라면, 뒤에 문장 B를 그냥 붙여줌
                    for j in range(a_end, len(current_chunk)):
                        tokens_b.extend(current_chunk[j])

                # A와 B를 랜덤이던, 그렇지 않던, 다 만들고 나서 처리
                """최대 길이에 맞춰 각각의 토큰 값들에서 앞뒤로 랜덤하게 문장을 자른다."""
                while True:
                    total_length = len(tokens_a) + len(tokens_b)
                    if total_length <= max_num_tokens:
                        break

                    # 좀 더 긴쪽의 문장을 길이에 맞게 날려주려나 보다.
                    trunc_tokens = tokens_a if len(
                        tokens_a) > len(tokens_b) else tokens_b
                    # trunc_tokens은 무조건 1보다 커야함.
                    assert len(trunc_tokens) >= 1

#                         print(trunc_tokens)

                    # 언제는 앞부터 날리고 언제는 뒤부터 날리고 싶을 수 있으니, 랜덤으로 처리.
                    if rng.random() < 0.5:
                        del trunc_tokens[0]
                    else:
                        trunc_tokens.pop()
                
                # 최소 토큰에 단어가 한개이상씩은 있어야함...
                assert len(tokens_a) >= 1
                assert len(tokens_b) >= 1

                # 기초 양식과, A/B 문장 구분자를 넣어준다.
                tokens = []
                segment_ids = []
                tokens.append("[CLS]")
                segment_ids.append(0)
                for token in tokens_a:
                    tokens.append(token)
                    segment_ids.append(0)

                tokens.append("[SEP]")
                segment_ids.append(0)

                for token in tokens_b:
                    tokens.append(token)
                    segment_ids.append(1)
                tokens.append("[SEP]")
                segment_ids.append(1)


#                     (tokens, masked_lm_positions,
#                      masked_lm_labels) = create_masked_lm_predictions(
#                          tokens, masked_lm_prob, max_predictions_per_seq, vocab_words, rng)		# 만들어진 전체 sequence의 특정 token index에 [MASK] 를 수행
                """Pre-Train에서 사용할 masked LM을 설정"""
                cand_indexes = []
                # [MASK] 를 삽입할 token 후보 리스트를 생성
                # token_index는 순수하게 0부터 순서대로 토큰이 들어간 순서가 된다.
                for (token_index, token) in enumerate(tokens):
                    if token == "[CLS]" or token == "[SEP]":
                        continue
                    cand_indexes.append(token_index)

#                 rng.shuffle(cand_indexes)

                output_tokens = list(tokens)

                # mask된 값을 예측해야되니 데이터 셋으로 만들어 둘 예정...
                masked_lm = collections.namedtuple(
                    "masked_lm", ["index", "label"])  # pylint: disable=invalid-name

                num_to_predict = min(max_predictions_per_seq,					# [MASK] 를 삽입할 token의 개수를 현재 token 중에서 15%의 확률로 선택
                                     max(1, int(round(len(tokens) * masked_lm_prob))))  # 만약 그 값이 20보다 크다면, 20개의 token만 [MASK]로 변환

                masked_lms = []
                covered_indexes = set()
                for index in cand_indexes:
                    # 앞에서 지정한 개수 만큼한 [MASK]
                    if len(masked_lms) >= num_to_predict:
                        break
                    if index in covered_indexes:
                        continue
                    covered_indexes.add(index)

                    masked_token = None
                    # 80% of the time, replace with [MASK]
                    if rng.random() < 0.8:							# 그 중, 80%는 [MASK]로 변환
                        masked_token = "[MASK]"
                    else:
                        # 10% of the time, keep original
                        if rng.random() < 0.5:							# 나머지 20%의 확률 중, 절반인 10%는 원본 유지
                            masked_token = tokens[index]
                        # 10% of the time, replace with random word
                        else:									# 나머지 10%는 랜덤으로 replace
                            masked_token = vocab_words[rng.randint(
                                0, len(vocab_words) - 1)]

                    output_tokens[index] = masked_token

                    masked_lms.append(masked_lm(index=index, label=tokens[index]))

                masked_lms = sorted(masked_lms, key=lambda x: x.index)

                masked_lm_positions = []
                masked_lm_labels = []
                for p in masked_lms:
                    # masked된 부분에 대한 정답을 정리해놓음
                    masked_lm_positions.append(p.index)
                    masked_lm_labels.append(p.label)

#                     print('output_tokens : ', output_tokens)
#                     print('masked_lms : ', masked_lms)
#                     print('masked_lm_positions : ', masked_lm_positions)
#                     print('masked_lm_labels : ', masked_lm_labels)

                # 트레이닝할 데이터를 쓰기좋고, 보기좋게 정리해둠 __str__로 내용을 전부 파악 가능함.
                instance = TrainingInstance(
                    tokens=tokens,
                    segment_ids=segment_ids,
                    is_random_next=is_random_next,
                    masked_lm_positions=masked_lm_positions,
                    masked_lm_labels=masked_lm_labels)
                instances.append(instance)
            current_chunk = []
            current_length = 0
        i += 1
        # 여기까지 수행되면 2문장을 합쳐서, [SEP]를 붙혀주고, [MASK]를 찾아, 해당 위치를 저장해놓은 instances를 만들어놓게 된다.
#         print('instances : ', instances)
    return instances

In [16]:
tf.logging.info('make vocab dict')
vocab_words = list(tokenizer.vocab.keys())    # 사전 배열화

instances = []
# print(vocab_words)
tf.logging.info('make tokens')
for _ in tqdm(range(dupe_factor), desc='BERT_Pre_Trained_DATA_FITTING'):
    # all_documents는 shape (문서개수,문장개수,bpe 단어개수) 가 된다.
    for document_index in range(len(all_documents)):  # 가장 앞단 shape인, 문서마다 반복
        instances.extend(					# [CLS] 문장 A [SEP] 문장 B [SEP] 꼴을 만들어 줌
            create_instances_from_document(
                all_documents, document_index, max_seq_length, short_seq_prob,
                masked_lm_prob, max_predictions_per_seq, vocab_words, rng))

# rng.shuffle(instances)
print( instances)
# output_files = './wiki_20190620_small_512_tf.record'.split(",")
# tf.logging.info("*** Writing to output files ***")
# for output_file in output_files:
#     tf.logging.info("  %s", output_file)

# write_instance_to_example_files(instances, tokenizer, max_seq_length,	# output 파일에 write를 수행하는 부분
#                                 max_predictions_per_seq, output_files)

# MASK, SEP, 문장합치기를 포함한 완전한 Training셋의 전처리가 종료되게 됨.

INFO:tensorflow:make vocab dict
INFO:tensorflow:make tokens


BERT_Pre_Trained_DATA_FITTING:   0%|          | 0/1 [00:00<?, ?it/s]

[['박', '##문', '##규', ',', '1805', '##년', '1888', '##년', '는', '조선', '##시대', '##의', '시인', '겸', '문신', '##이', '##다', '##.'], ['자는', '제', '##홍', ',', '호', '##는', '운', '##소', '##자', '천', '##유', '##자', '.'], ['본관', '순', '##창', '박', '##유형', '의', '아들', '##.'], ['장성', '##한', '후', '상업', '등', '##으로', '많', '##은', '재산', '##을', '모', '##았', '##으나', '방', '##탕', '##하여', '가', '##산', '##을', '탕', '##진', '##하', '##였', '##다', '##.'], ['그', '후', '40', '##세부', '##터', '면', '##학', '##의', '뜻', '##을', '가', '##다', '##듬', '##고', '시', '##문', '공부', '##를', '하', '##여', '고시', '수', '##만', '편', '##을', '외', '##웠', '##으며', '##,', '근', '##체', '##시', '에', '능', '##하여', '청나라', '##에', '##까지', '명성', '##을', '떨', '##쳤', '##다', '##.'], ['1887', '##년', '8', '##3', '##세', '##에', '개성', '##별', '##시', '##문', '##과', '에', '병', '##과', '로', '급제', '##,', '최고', '##령', '과거', '급제', '##자라', '##는', '기록', '##을', '남겼', '##다', '##.'], ['그', '해', '고종', '##의', '특', '##명', '##으로', '병', '##조', '##참', '##지', '##,', '병', '##조', '##참', '##의', '##를', '거쳐', '#

[['명', '말', '##이', '되', '##면', '양', '##쯔', '강', '중', '##류', '##지역', '##이', '새로운', '곡', '##창', '##지대', '##가', '되', '##어', '경제', '##적', '분', '##업', '##화', '##가', '이루', '##어졌', '##다', '##.'], ['상업', '##의', '발달', '##은', '상인', '집단', '##을', '배출', '##하', '##였', '##는데', '##,', '특히', '산', '##시', '상인', '##과', '신', '##안', '상인', '##의', '활동', '##이', '컸', '##다', '##.'], ['이', '##들', '##에', '의해', '강남', '##의', '수', '##공업', '제품', '##이', '각지', '##로', '팔', '##려', '나갔', '##고', '##,', '각', '지역', '##의', '특', '##산물', '##과', '쌀', '##,', '면', '##화', '등', '##의', '원', '##료', '##가', '강남', '##지방', '##으로', '들어', '##왔', '##다', '##.'], ['쌀', '##,', '소금', '##,', '직', '##물', '##,', '도', '##자기', '##,', '차', '등', '##이', '전국', '##적', '##인', '교역', '##품', '##이', '##었', '##다', '##.'], ['명', '##대', '중', '##엽', '이후', '##로', '상업', '##의', '발달', '##이', '특히', '두', '##드러', '##졌으며', '##,', '강남', '지역', '##에서', '생산', '##된', '상품', '##을', '구입', '##하', '##기', '위해', '서양', '##의', '상인', '##이', '찾아오', '##기도', '하', '##였', '##다', '##.'], ['마카'

a_end :  5
[['그리고', '춘', '##추', '전국', '시대', '##에', '제자', '##백', '##가', '##가', '각종', '사상', '##을', '주', '##창', '##하', '##고', '제', '##후', '##들', '##에게', '유', '##세', '##하', '##면서', '삼', '##황', '##오', '##제', '신화', '##가', '창조', '##되', '##어', '틀', '##을', '갖추', '##어', '나갔', '##다', '##.'], ['오', '##제', '신화', '##의', '경우', '음', '##양', '##오', '##행', '##설', '##이', '유행', '##한', '이후', '##에', '5', '##명', '##의', '제', '##왕', '##이', '신화', '##로서', '정', '##립', '##되', '##기', '시작', '##한', '것', '##으로', '보인다', '##.'], ['이렇게', '후', '##대', '##에', '재', '##창조', '##된', '신화', '##이기', '때문', '##에', '삼', '##황', '##과', '오', '##제의', '구성원', '##은', '제자', '##백', '##가', '##의', '주장', '##에', '따라', '천', '##차', '##만', '##별', '##이', '##다', '##.'], ['춘', '##추', '전국', '시대', '##에서', '위', '##진', '##남북', '##조', '시대', '##에', '이르', '##는', '기간', '동안', '삼', '##황', '##오', '##제', '신화', '##는', '계속', '재', '##창조', '##되', '##었', '##다', '##.'], ['삼', '##황', '##오', '##제', '##는', '근대', '이전', '##의', '중국', '##에서', '역사', '##적', '사실', '##로', '오랜', '기간

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




a_end :  1
[['허', '##영', '##란', ',', '1980', '##년', '9', '##월', '16', '##일', '은', '대한민국', '##의', '배우', '##다', '##.']]
[['다', '##퉁', '구', ',', '는', '중화', '인민', '공화국', '안', '##후', '##이성', '화', '##이', '##난', '시', '##의', '현', '##급', '행정', '##구역', '##이', '##다', '##.'], ['넓이', '##는', '314', '##km', '##이고', '##,', '인구', '##는', '2007', '##년', '기준', '##으로', '[UNK]'], ['1', '##개', '가', '##도', '##,', '3', '##개', '진', '##,', '1', '##개', '향', '##을', '관할', '##한다', '##.']]
a_end :  1
[['셰', '##자', '##지', '구', ',', '는', '중화', '인민', '공화국', '안', '##후', '##이성', '화', '##이', '##난', '시', '##의', '현', '##급', '행정', '##구역', '##이', '##다', '##.'], ['넓이', '##는', '27', '##3', '##km', '##이고', '##,', '인구', '##는', '2007', '##년', '기준', '##으로', '[UNK]'], ['5', '##개', '가', '##도', '##,', '4', '##개', '진', '##,', '1', '##개', '향', '##.'], ['1', '##게', '민족', '##향', '##을', '관할', '##한다', '##.']]
a_end :  2
[['5', '##개', '가', '##도', '##,', '4', '##개', '진', '##,', '1', '##개', '향', '##.'], ['1', '##게', '민족', '##향', '##을', '관할', '

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




a_end :  2
[['미', '##자는', '큰', '병원', '##에서', '알', '##츠', '##하이', '##머', '진단', '##을', '받', '##는다', '##.'], ['딸', '##과', '통화', '##하', '##면서', '##,', '미', '##자는', '돈', '##에', '대한', '것', '##도', '치', '##매', '##에', '대한', '것', '##도', '말', '##을', '못', '한다', '##.'], ['학부모', '##들', '##이', '미', '##자', '##에게', '나이', '##든', '어머니', '##로서', '희', '##진', '어머니', '##와', '합의', '##를', '보', '##라고', '떠', '##맡', '##겨', '##지지', '##만', '##,', '정', '##작', '희', '##진', '어머니', '##와', '만나', '##자', '그런', '얘', '##기', '##를', '해야', '한다는', '사실', '자체', '##를', '잊', '##어', '##버리', '##고', '농', '##사', '##에', '관한', '잡', '##담', '##만', '하', '##다가', '##,', '뒤', '##돌아서', '##서', '그것', '##을', '잊', '##어', '##버렸', '##다는', '사실', '##을', '떠', '##올리', '##고', '##는', '두려워', '##한다', '##.'], ['미', '##자는', '기', '##범', '##의', '아버지', '##에게', '합의', '##금', '##으로', '쓸', '500', '##만', '##원', '##을', '빌', '##려', '##보', '##려고', '하지만', '거절', '##당한', '##다', '##.'], ['절', '##망', '##한', '미', '##자는', '비', '##를', '맞', '##은', '모습', '##으로', '강', '노', '##인', '

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
# log txt로 각 instance 별 추출
import os
try:
    if not os.path.exists('./create_data_log'):
        os.makedirs('./create_data_log')
except OSError:
    print ('Error: Creating directory. ./create_data_log')    

for i in tqdm(range(len(instances)), desc='BERT_Pre_Trained_DATA_txt_output'):
#     if i == 0:
    with open('./create_data_log/'+'_'.join(instances[i].__dict__()['tokens'][1:15])+'.txt','w',encoding='utf-8') as result_writer:
        result_writer.write(instances[i].__str__())    

# import json

# for i in tqdm(range(len(instances)), desc='BERT_Pre_Trained_DATA_json_output'):
# #     if i == 0:
#     with open('./data_process_log/'+'_'.join(instances[i].__dict__()['tokens'][1:15])+'.json','w',encoding='utf-8') as result_writer:
#         result_writer.write(str(json.dumps(instances[i].__dict__())))
        
